In [124]:
import ibis
from ibis import _
import streamlit as st

conn = ibis.duckdb.connect(extensions=["spatial"])

state_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-state-territory.parquet"
county_boundaries = "https://data.source.coop/cboettig/us-boundaries/us-county.parquet"
states = conn.read_parquet(state_boundaries).rename(state_id = "STUSPS", state = "NAME")
county = conn.read_parquet(county_boundaries).rename(county = "NAMELSAD", state = "STATE_NAME")

votes = conn.read_csv("landvote.csv")
votes.count().execute()

vote = (votes
       .filter(_["Jurisdiction Type"] == "County")
       .rename(county = "Jurisdiction Name", state_id = "State")
       .mutate(key = _.county + ibis.literal('-') + _.state_id)
       .rename(amount = 'Conservation Funds at Stake', yes = '% Yes')
       .mutate(amount_n=_.amount.replace('$', '').replace(',', '').cast('float'))
       .mutate(log_amount=_.amount_n.log())
       .mutate(year=_['Date'].year().cast('int32'))
       .select('key', 'Status', 'yes', 'year', 'amount', 'log_amount', )
       )
df = (county
      .join(states.select("state", "state_id"), "state")
      .mutate(key = _.county + ibis.literal('-') + _.state_id)
      .select('key', 'geometry')
      .right_join(vote, "key")
      .drop('key_right')
     )



In [133]:
import leafmap.maplibregl as leafmap
m = leafmap.Map(style="positron")


gdf = df.filter(_.year==2022).execute()

outcome = [
      'match',
      ['get', 'Status'], 
      "Pass", '#2E865F',
      "Fail", '#FF3300', 
      '#ccc'
    ]
paint = {"fill-extrusion-color": outcome, 
         "fill-extrusion-opacity": 0.7,
         "fill-extrusion-height": ["*", ["get", "log_amount"], 5000],
        }

#m.add_geojson("vote.geojson")
m.add_gdf(gdf, "fill-extrusion", paint = paint)
m

FloatProgress(value=0.0, layout=Layout(width='auto'), style=ProgressStyle(bar_color='black'))

Map(height='600px', map_options={'bearing': 0, 'center': (0, 20), 'pitch': 0, 'style': 'https://tiles.openfree…

In [129]:
import numpy as np 
np.log(440000000)

19.90228528487658